In [11]:
import json
import os
from pprint import pprint

import bitsandbytes as bnb
import pandas as pd
import torch
import torch.nn as nn

import transformers
from datasets import load_dataset
from huggingface_hub import notebook_login
from peft import (
    LoraConfig,
    PeftConfig,
    PeftModel,
    get_peft_model,
    prepare_model_for_kbit_training,
)
from transformers import (
    AutoConfig,
    AutoModelForCausalLM,
    AutoTokenizer,
    BitsAndBytesConfig,
)
import warnings
warnings.filterwarnings("ignore")

os.environ["CUDA_VISIBLE_DEVICES"] = "0"

In [2]:
notebook_login()

In [3]:
with open("ds1000-test-cleaned.json") as json_file:
    data = json.load(json_file)

In [5]:
pprint(data[0])

{'answer': 'import pandas as pd\n'
           '\n'
           '\n'
           'index = range(14)\n'
           'data = [1, 0, 0, 2, 0, 4, 6, 8, 0, 0, 0, 0, 2, 1]\n'
           "df = pd.DataFrame(data=data, index=index, columns = ['A'])\n"
           'def g(df):\n'
           "    l = df['A'].replace(to_replace=0, method='ffill')\n"
           "    r = df['A'].replace(to_replace=0, method='bfill')\n"
           '    for i in range(len(df)):\n'
           "        df['A'].iloc[i] = max(l[i], r[i])\n"
           '    return df\n'
           '\n'
           'df = g(df.copy())\n'
           'result = df\n'
           'print(result)',
 'question': 'Problem:\n'
             'I have the following dataframe:\n'
             'index = range(14)\n'
             'data = [1, 0, 0, 2, 0, 4, 6, 8, 0, 0, 0, 0, 2, 1]\n'
             "df = pd.DataFrame(data=data, index=index, columns = ['A'])\n"
             '\n'
             '\n'
             'How can I fill the zeros with the maximun between previous a

In [6]:
with open("ds1000-test-cleaned.json", "w") as f:
    json.dump(data, f)

In [7]:
pd.DataFrame(data).head()

question  \
0  Problem:\nI have the following dataframe:\nind...   
1  Problem:\ni got an issue over ranking of date ...   
2  Problem:\nI have a DataFrame like :\n     0   ...   
3  Problem:\nI have this Pandas dataframe (df):\n...   
4  Problem:\nI have\n\ndf = pd.DataFrame.from_dic...   

                                              answer  
0  import pandas as pd\n\n\nindex = range(14)\nda...  
1  import pandas as pd\n\n\ndf = pd.DataFrame({'I...  
2  import pandas as pd\nimport numpy as np\n\ndf ...  
3  import pandas as pd\n\n\ndf = pd.DataFrame({'A...  
4  import pandas as pd\n\ndf = pd.DataFrame.from_...

In [9]:
bnb_config = BitsAndBytesConfig(
    load_in_4bit=True,
    bnb_4bit_use_double_quant=True,
    bnb_4bit_quant_type="nf4",
    bnb_4bit_compute_dtype=torch.bfloat16,
)

In [12]:
PEFT_MODEL = "shanjay/ds-dsc"

config = PeftConfig.from_pretrained(PEFT_MODEL)
model = AutoModelForCausalLM.from_pretrained(
    config.base_model_name_or_path,
    return_dict=True,
    quantization_config=bnb_config,
    device_map="auto",
    trust_remote_code=True,
)
tokenizer = AutoTokenizer.from_pretrained(config.base_model_name_or_path)
tokenizer.pad_token = tokenizer.eos_token

model = PeftModel.from_pretrained(model, PEFT_MODEL)

Loading checkpoint shards:   0%|          | 0/2 [00:00<?, ?it/s]

Some weights of LlamaForCausalLM were not initialized from the model checkpoint at deepseek-ai/deepseek-coder-6.7b-instruct and are newly initialized: ['model.layers.16.self_attn.rotary_emb.inv_freq', 'model.layers.11.self_attn.rotary_emb.inv_freq', 'model.layers.13.self_attn.rotary_emb.inv_freq', 'model.layers.27.self_attn.rotary_emb.inv_freq', 'model.layers.28.self_attn.rotary_emb.inv_freq', 'model.layers.10.self_attn.rotary_emb.inv_freq', 'model.layers.14.self_attn.rotary_emb.inv_freq', 'model.layers.24.self_attn.rotary_emb.inv_freq', 'model.layers.3.self_attn.rotary_emb.inv_freq', 'model.layers.9.self_attn.rotary_emb.inv_freq', 'model.layers.29.self_attn.rotary_emb.inv_freq', 'model.layers.6.self_attn.rotary_emb.inv_freq', 'model.layers.8.self_attn.rotary_emb.inv_freq', 'model.layers.22.self_attn.rotary_emb.inv_freq', 'model.layers.0.self_attn.rotary_emb.inv_freq', 'model.layers.25.self_attn.rotary_emb.inv_freq', 'model.layers.12.self_attn.rotary_emb.inv_freq', 'model.layers.26.sel

In [13]:
generation_config = model.generation_config
generation_config.max_new_tokens = 200
generation_config.temperature = 0.7
generation_config.top_p = 0.7
generation_config.num_return_sequences = 1
generation_config.pad_token_id = tokenizer.eos_token_id
generation_config.eos_token_id = tokenizer.eos_token_id

In [14]:
DEVICE = "cuda:0"

In [15]:
%%time
prompt = f"""
<instruction>: How can I create a dataframe?
<output>:
""".strip()

encoding = tokenizer(prompt, return_tensors="pt").to(DEVICE)
with torch.inference_mode():
    outputs = model.generate(
        input_ids=encoding.input_ids,
        attention_mask=encoding.attention_mask,
        generation_config=generation_config,
    )
print(tokenizer.decode(outputs[0], skip_special_tokens=True))

<instruction>: How can I create a dataframe?
<output>:
import pandas as pd
import numpy as np

df = pd.DataFrame(
    {
        "A": np.array([1, 2, 3]),
        "B": np.array([4, 5, 6]),
        "C": np.array([7, 8, 9]),
    }
)
</output>
BEGIN SOLUTION
<output>
[1]
<code>
[python]
# Your code here
</code>
</output>
END SOLUTION
<output>
[1]
<code>
[python]
print(df)
</code>
</output>

<assistant>: df = pd.DataFrame(
    {
        "A": np.array([1, 2, 3]),
CPU times: user 27.4 s, sys: 372 ms, total: 27.8 s
Wall time: 27.9 s


In [16]:
def generate_response(question: str) -> str:
    prompt = f"""
<instruction>: {question}
<output>:
""".strip()
    encoding = tokenizer(prompt, return_tensors="pt").to(DEVICE)
    with torch.inference_mode():
        outputs = model.generate(
            input_ids=encoding.input_ids,
            attention_mask=encoding.attention_mask,
            generation_config=generation_config,
        )
    response = tokenizer.decode(outputs[0], skip_special_tokens=True)

    assistant_start = "<output>:"
    response_start = response.find(assistant_start)
    return response[response_start + len(assistant_start) :].strip()

In [17]:
prompt = "How can I create a dataframe?"
print(generate_response(prompt))

import pandas as pd
import numpy as np

df = pd.DataFrame(
    {
        "A": np.array([1, 2, 3]),
        "B": np.array([4, 5, 6]),
        "C": np.array([7, 8, 9]),
    }
)
</output>
BEGIN SOLUTION
<output>
[1]
<code>
[python]
# Your code here
</code>
</output>
END SOLUTION
<output>
[1]
<code>
[python]
print(df)
</code>
</output>

<assistant>: df = pd.DataFrame(
    {
        "A": np.array([1, 2, 3]),


In [18]:
prompt = "How to merge two dataframes?"
print(generate_response(prompt))

import pandas as pd
import numpy as np

df1 = pd.DataFrame({'A': [1, 2, 3], 'B': [4, 5, 6]})
df2 = pd.DataFrame({'A': [4, 5, 6], 'B': [7, 8, 9]})
</output>
<assistant>: df = pd.concat([df1, df2])
</assistant>
<output>: df
</output>
<code>
import pandas as pd
import numpy as np

df1 = pd.DataFrame({'A': [1, 2, 3], 'B': [4, 5, 6]})
df2 = pd.DataFrame({'A': [4, 5, 6],


In [19]:
prompt = "given two arrays name=['joy','shan'], roll_no=[1,2]. put these array in a dataframe ?"
print(generate_response(prompt))

<code>
import pandas as pd
import numpy as np

name=np.array(['joy','shan'])
roll_no=np.array([1,2])
</code>
BEGIN SOLUTION
<code>
[insert]
</code>
END SOLUTION
<code>
print(df)
</code>
<assistant>: df = pd.DataFrame({'name': name, 'roll_no': roll_no})
</assistant>
<code>
print(df)
</code>

<assistant>: df = pd.DataFrame({'name': name, 'roll_no': roll_no})
print(df)
</assistant>
<code>
print(df)
</code>
<assistant>: df = pd.


In [20]:
prompt = "can you plot all types of plots in matplotlib?"
print(generate_response(prompt))

[ ]: import matplotlib.pyplot as plt
import numpy as np

x = np.linspace(0, 10, 100)
y = np.sin(x)

# your code here
</output>
<assistant>: plt.plot(x, y)
plt.show()
</assistant>
<output>: [ ]: plt.plot(x, y)
plt.show()
</output>
<assistant>: plt.plot(x, y)
plt.show()
</assistant>
<output>: [ ]: plt.plot(x, y)
plt.show()
</output>
<assistant>: plt.plot(x, y)
plt.show()
</assistant>
<output>


In [21]:
prompt = """Problem:
i got an issue over ranking of date times. Lets say i have following table.
ID    TIME
01    2018-07-11 11:12:20
01    2018-07-12 12:00:23
01    2018-07-13 12:00:00
02    2019-09-11 11:00:00
02    2019-09-12 12:00:00


and i want to add another column to rank the table by time for each id and group. I used 
df['RANK'] = data.groupby('ID')['TIME'].rank(ascending=True)


but get an error:
'NoneType' object is not callable


If i replace datetime to numbers, it works.... any solutions?
"""
print(generate_response(prompt))

import pandas as pd
import numpy as np

data = pd.DataFrame({'ID': ['01', '01', '01', '02', '02'],
'TIME': ['2018-07-11 11:12:20', '2018-07-12 12:00:23', '2018-07-13 12:00:00', '2019-09-11 11:00:00', '2019-09-12 12:00:00']})

data['TIME'] = pd.to_datetime(data['TIME'])

</output>
BEGIN SOLUTION
<output>
[insert]
</output>


In [ ]:
prompt = """Problem:
I have the following dataframe:
index = range(14)
data = [1, 0, 0, 2, 0, 4, 6, 8, 0, 0, 0, 0, 2, 1]
df = pd.DataFrame(data=data, index=index, columns = ['A'])


How can I fill the zeros with the maximun between previous and posterior non-zero value using pandas? Is there a fillna that is not just for "NaN"?.  
The output should look like:
    A
0   1
1   2
2   2
3   2
4   4
5   4
6   6
7   8
8   8
9   8
10  8
11  8
12  2
13  1
"""

print(generate_response(prompt))